
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning">
</div>



# Automated Model Development with AutoML

In this demo, we will demonstrate how to initiate AutoML experiments both through the user-friendly AutoML UI and programmatically using the AutoML API. When using the API, we will demonstrate some custom functionalities such as feature table integration and custom split ratios for train, validation and test.

**Learning Objectives:**

*By the end of this demo, you will be able to:*

* Start an AutoML experiment via the AutoML UI.

* Start an AutoML experiment via the AutoML API.

* Open and edit a notebook generated by AutoML.

* Identify the best model generated by AutoML based on a given metric.

* Modify the best model generated by AutoML.



## REQUIRED - SELECT CLASSIC COMPUTE
Before executing cells in this notebook, please select your classic compute cluster in the lab. Be aware that **Serverless** is enabled by default.
Follow these steps to select the classic compute cluster:
1. Navigate to the top-right of this notebook and click the drop-down menu to select your cluster. By default, the notebook will use **Serverless**.
1. If your cluster is available, select it and continue to the next cell. If the cluster is not shown:
   - In the drop-down, select **More**.
   - In the **Attach to an existing compute resource** pop-up, select the first drop-down. You will see a unique cluster name in that drop-down. Please select that cluster.
  
**NOTE:** If your cluster has terminated, you might need to restart it in order to select it. To do this:
1. Right-click on **Compute** in the left navigation pane and select *Open in new tab*.
1. Find the triangle icon to the right of your compute cluster name and click it.
1. Wait a few minutes for the cluster to start.
1. Once the cluster is running, complete the steps above to select your cluster.

## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **16.3.x-cpu-ml-scala2.12**


## Classroom Setup

Before starting the demo, run the provided classroom setup script. This script will define configuration variables necessary for the demo. Execute the following cell:

In [0]:
%run ../Includes/Classroom-Setup-3.1

  Using cached databricks_sdk-0.36.0-py3-none-any.whl.metadata (38 kB)
Using cached databricks_sdk-0.36.0-py3-none-any.whl (569 kB)
  Attempting uninstall: databricks-sdk
    Found existing installation: databricks-sdk 0.30.0
    Not uninstalling databricks-sdk at /databricks/python3/lib/python3.12/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-4ebe0852-35af-442d-b80a-6f7aabfd0986
    Can't uninstall 'databricks-sdk'. No files were found to uninstall.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


2025/08/07 04:23:21 INFO databricks.ml_features._compute_client._compute_client: Setting columns ['CustomerID'] of table 'dbacademy.labuser11091541_1754532261.customer_churn_features' to NOT NULL.
2025/08/07 04:23:22 INFO databricks.ml_features._compute_client._compute_client: Setting Primary Keys constraint ['CustomerID'] on table 'dbacademy.labuser11091541_1754532261.customer_churn_features'.
2025/08/07 04:23:27 INFO databricks.ml_features._compute_client._compute_client: Created feature table 'dbacademy.labuser11091541_1754532261.customer_churn_features'.


**Other Conventions:**

Throughout this demo, we'll refer to the object `DA`. This object, provided by Databricks Academy, contains variables such as your username, catalog name, schema name, working directory, and dataset locations. Run the code block below to view these details:

In [0]:
print(f"Username:          {DA.username}")
print(f"Catalog Name:      {DA.catalog_name}")
print(f"Schema Name:       {DA.schema_name}")
print(f"Working Directory: {DA.paths.working_dir}")
print(f"User DB Location:  {DA.paths.datasets}")

Username:          labuser11091541_1754532261@vocareum.com
Catalog Name:      dbacademy
Schema Name:       labuser11091541_1754532261
Working Directory: /Volumes/dbacademy/ops/labuser11091541_1754532261@vocareum_com
User DB Location:  NestedNamespace (california_housing='/Volumes/dbacademy_california_housing/v02', cdc_diabetes='/Volumes/dbacademy_cdc_diabetes/v01', telco='/Volumes/dbacademy_telco/v01', banking='/Volumes/dbacademy_banking/v01')



## Prepare Data

For this demonstration, we will utilize a fictional dataset from a Telecom Company, which includes customer information. This dataset encompasses **customer demographics**, including gender, as well as internet subscription details such as subscription plans and payment methods.

A table with all features is already created for you.

**Table name: `customer_churn`**

To get started, execute the code block below and review the dataset schema.

In [0]:
churn_data = spark.sql("SELECT * FROM customer_churn")
display(churn_data)

CustomerID Gender SeniorCitizen Partner InternetService Contract PaperlessBilling PaymentMethod Churn 0 Female 0 Yes DSL Month-to-month Yes Electronic check No 1 Male 0 No DSL One year No Mailed check No 2 Male 0 No DSL Month-to-month Yes Mailed check Yes 3 Male 0 No DSL One year No Bank transfer (automatic) No 4 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes 5 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes 6 Male 0 No Fiber optic Month-to-month Yes Credit card (automatic) No 7 Female 0 No DSL Month-to-month No Mailed check No 8 Female 0 Yes Fiber optic Month-to-month Yes Electronic check Yes 9 Male 0 No DSL One year No Bank transfer (automatic) No 10 Male 0 Yes DSL Month-to-month Yes Mailed check No 11 Male 0 No No Two year No Credit card (automatic) No 12 Male 0 Yes Fiber optic One year No Credit card (automatic) No 13 Male 0 No Fiber optic Month-to-month Yes Bank transfer (automatic) Yes 14 Male 0 No Fiber optic Month-to-month Yes Electronic check No 15 Female 0 Yes Fiber optic Two year No Credit card (automatic) No 16 Female 0 No No One year No Mailed check No 17 Male 0 No Fiber optic Two year No Bank transfer (automatic) No 18 Female 0 Yes DSL Month-to-month No Credit card (automatic) Yes 19 Female 0 No Fiber optic Month-to-month Yes Electronic check No 20 Male 1 No DSL Month-to-month Yes Electronic check Yes 21 Male 0 Yes No One year No Bank transfer (automatic) No 22 Male 0 No No Month-to-month No Mailed check Yes 23 Female 0 Yes DSL Two year Yes Credit card (automatic) No 24 Male 0 Yes DSL Month-to-month No Credit card (automatic) No 25 Female 0 No DSL Month-to-month Yes Bank transfer (automatic) No 26 Male 0 Yes Fiber optic Month-to-month Yes Electronic check Yes 27 Male 0 Yes DSL Month-to-month No Electronic check Yes 28 Male 0 Yes DSL Two year Yes Credit card (automatic) No 29 Female 0 No DSL Month-to-month Yes Mailed check Yes 30 Female 1 Yes Fiber optic Two year Yes Credit card (automatic) No 31 Male 1 Yes Fiber optic Month-to-month Yes Credit card (automatic) No 32 Female 0 Yes DSL One year No Mailed check No 33 Male 0 No No Month-to-month No Bank transfer (automatic) No 34 Male 1 No DSL Month-to-month No Bank transfer (automatic) No 35 Female 0 Yes Fiber optic Two year No Bank transfer (automatic) No 36 Male 0 No Fiber optic Month-to-month Yes Electronic check Yes 37 Female 0 No Fiber optic Month-to-month Yes Credit card (automatic) No 38 Male 0 No Fiber optic Month-to-month Yes Electronic check Yes 39 Female 0 No Fiber optic Month-to-month Yes Bank transfer (automatic) Yes 40 Male 0 Yes DSL One year No Mailed check No 41 Female 0 Yes DSL Two year Yes Credit card (automatic) No 42 Female 0 Yes No One year No Mailed check No 43 Female 0 No DSL Two year Yes Credit card (automatic) No 44 Female 0 Yes DSL Month-to-month Yes Electronic check No 45 Female 0 No Fiber optic Month-to-month Yes Electronic check No 46 Male 0 No DSL Month-to-month No Mailed check No 47 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes 48 Male 0 No DSL Two year Yes Credit card (automatic) No 49 Female 0 Yes DSL Two year Yes Credit card (automatic) No 50 Female 1 No Fiber optic Month-to-month Yes Electronic check No 51 Female 0 No Fiber optic Month-to-month Yes Credit card (automatic) Yes 52 Female 1 Yes DSL Month-to-month Yes Credit card (automatic) No 53 Female 1 Yes Fiber optic Month-to-month Yes Credit card (automatic) Yes 54 Female 1 Yes DSL One year Yes Credit card (automatic) No 55 Male 1 No Fiber optic Month-to-month Yes Electronic check Yes 56 Female 0 Yes Fiber optic One year Yes Credit card (automatic) No 57 Male 1 Yes Fiber optic One year Yes Electronic check No 58 Female 0 Yes No Two year No Credit card (automatic) No 59 Female 0 No Fiber optic Two year Yes Credit card (automatic) No 60 Female 0 Yes Fiber optic Month-to-month Yes Electronic check No 61 Male 0 No Fiber optic Month-to-month Yes Bank transfer (automatic) No 62 Male 0 Yes DSL Two year No Bank transfer (automatic) No 63 

## AutoML Experiment with UI

Databricks AutoML supports experimentation via the UI and the API. Thus, **in the first section of this demo we will demonstrate how to create an experiment using the UI**. Then, show how to create the same experiment via the API.


### Create AutoML Experiment

Let's initiate an AutoML experiment to construct a baseline model for predicting customer churn. The target field for this prediction will be the `Churn` field.

Follow these step-by-step instructions to create an AutoML experiment:

1. Navigate to the **Experiments** section in Databricks.


2. Click on **Classification**.

  ![automl-create-experiment-v1](../Includes/images/automl-create-experiment-v2.png)

3. Choose a cluster to execute the experiment.

4. Select the **catalog > database > `customers_churn` table**, which was created in the previous step, as the input training dataset.

5. Specify **`Churn`** as the prediction target.

6. Deselect the **CustomerID** field as it's not needed as a feature.

7. In the **Advanced Configuration** section, set the **Timeout** to **5 minutes**.

8. Enter a name for your experiment. Let's enter `Churn_Prediction_AutoML_Experiment` as experiment name.

![automl-input-fields-v1](../Includes/images/automl-input-fields-v1.png)

**Optional Advanced Configuration:**

![advanced-configurations-v1](../Includes/images/advanced-configurations-v1.png)

- You have the flexibility to choose the **evaluation metric** and your preferred **training framework**.

- If your dataset includes a timeseries field, you can define it when splitting the dataset.

9. Click on **Start AutoML**.


### View the Best Run

Once the experiment is finished, it's time to examine the best run:

1. Access the completed experiment in the **Experiments** section.

2. Identify the best model run by evaluating the displayed **metrics**. Alternatively, you can click on **View notebook for best model** to access the automatically generated notebook for the top-performing model.

![automl-completed-experiment-v1](../Includes/images/automl-completed-experiment-v2.png)

3. Utilize the **Chart** tab to compare and contrast the various models generated during the experiment.

You can find all details for the run  on the experiment page. There are different columns such as the framework used (e.g., `Scikit-Learn`, `XGBoost`), evaluation metrics (e.g., `Accuracy`, `F1 Score`), and links to the corresponding notebooks for each model. This allows you to make informed decisions about selecting the best model for your specific use case.

### View the Notebook

####**Instruction for viewing the notebook of the best run:**



+ **Click on the `"View notebook for best model"` link.**

+ **Review the notebook that created the best model.**


![automl-best-model-notebook-v1](../Includes/images/automl-best-model-notebook-v1.png)


+ **Edit the notebook as required.**
    + Identify the best model generated by AutoML based on a given metric and modify it as needed. The best model details, including the associated run ID, can be found in the MLflow experiment logs. Use the run ID to load the best model, make modifications, and save the modified model for deployment or further use.

## AutoML Experiment with API

In the previous section, we created an AutoML experiment using the user interface (UI) with basic functionalities. AutoML also supports advanced functionalities, such as **feature table integration** and **custom data split ratios**, which can enhance model performance and flexibility.

In this section, we will utilize the AutoML API to create an experiment incorporating these advanced features. By leveraging the API, we gain greater control over the experiment's configuration, enabling the customization of feature inputs and the specification of data splitting strategies.

### Set Features Table

AutoML supports the use of feature tables as input. During setup, a feature table (**`customer_churn_features`**) is created. In this section, we will utilize this feature table during model training. 



In [0]:
features_table_path = f"{DA.catalog_name}.{DA.schema_name}.customer_churn_features"

# View features tables
display(spark.sql(f"SELECT * FROM {features_table_path}"))

# Define the feature store lookups
feauture_store_lookups = [
    {
        "table_name": features_table_path,
        "lookup_key": ["CustomerID"]
    }
]

CustomerID AverageMonthlyCharges 0 29.85 1 55.5735294117647 2 54.075 3 40.90555555555556 4 75.825 5 102.5625 6 88.60909090909091 7 30.189999999999998 8 108.78750000000001 9 56.25725806451613 10 45.18846153846154 11 20.425 12 97.95 13 102.78163265306122 14 107.44200000000001 15 114.42246376811593 16 19.672115384615385 17 103.97535211267606 18 52.835 19 88.70952380952382 20 39.65 21 16.854166666666668 22 20.15 23 60.432758620689654 24 60.61836734693878 25 51.019999999999996 26 101.04574468085106 27 30.2 28 88.46458333333334 29 64.3 30 95.30915492957746 31 90.825 32 69.42407407407407 33 20.2 34 45.25 35 100.71805555555555 36 63.379999999999995 37 77.13695652173914 38 104.38970588235294 39 100.4909090909091 40 47.57 41 69.605 42 24.602941176470587 43 77.16587301587302 44 75.49615384615385 45 79.72857142857143 46 48.5 47 72.075 48 81.11153846153846 49 61.6536231884058 50 89.27325581395348 51 95.09333333333333 52 70.10600000000001 53 79.1625 54 74.27250000000001 55 97.36388888888888 56 100.17777777777778 57 107.21742424242424 58 26.302941176470586 59 109.07916666666667 60 100.15106382978725 61 90.845 62 41.138888888888886 63 53.172222222222224 64 95.25 65 81.36666666666666 66 77.66702127659575 67 80.55483870967741 68 18.618 69 88.735 70 49.05 71 20.974038461538463 72 110.921875 73 22.97741935483871 74 59.13333333333333 75 109.63392857142857 76 58.45326086956521 77 60.28125 78 70.37666666666668 79 27.035555555555554 80 79.35 81 51.39545454545455 82 70.98571428571428 83 103.03571428571429 84 19.864285714285714 85 102.08333333333333 86 63.29857142857142 87 22.020833333333332 88 20.15434782608696 89 34.80172413793103 90 85.67333333333333 91 74.7 92 86.57954545454545 93 109.33846153846154 94 103.59791666666666 95 77.27916666666667 96 66.8830985915493 97 22.77 98 21.292307692307695 99 100.58 100 20.2 101 19.45 102 94.88421052631578 103 45.86742424242424 104 111.93897058823529 105 20.04 106 101.43125 107 28.9890625 108 91.19302325581396 109 18.93402777777778 110 95.25272727272727 111 58.50480769230769 112 91.95581395348837 113 77.51756756756757 114 53.4921875 115 82.8 116 31.287499999999998 117 106.465 118 20.36951219512195 119 79.68888888888888 120 98.49017857142857 121 18.791666666666668 122 76.51666666666667 123 50.050000000000004 124 15.725 125 91.7469696969697 126 79.0925925925926 127 23.94375 128 19.75 129 56.131690140845066 130 93.51153846153846 131 60.106 132 48.65820895522388 133 35.45 134 40.625 135 27.632558139534886 136 77.32608695652173 137 19.96484375 138 20.5359649122807 139 70.45 140 89.24513888888889 141 70.45625 142 97.88934426229508 143 82.64140625 144 24.735211267605635 145 98.71846153846154 146 20.45 147 45.65 148 64.33166666666666 149 71.42666666666668 150 70.54375 151 93.64285714285714 152 113.29357142857143 153 84.11693548387096 154 18.916666666666668 155 82.34285714285714 156 82.81590909090909 157 19.086363636363636 158 64.0 159 25.16 160 58.81153846153846 161 79.61749999999999 162 67.6 163 74.68396226415095 164 21.263636363636365 165 19.76014492753623 166 68.25 167 86.86736111111111 168 45.710344827586205 169 20.0875 170 82.30813953488372 171 121.4 172 84.41071428571429 173 94.3433962264151 174 20.4546875 175 22.947058823529414 176 76.38000000000001 177 71.94285714285715 178 103.95 179 20.524590163934427 180 29.95 181 45.3 182 82.83125 183 74.34242424242424 184 85.51153846153846 185 24.8 186 51.1925 187 27.383333333333336 188 18.83076923076923 189 59.4775 190 73.79883720930232 191 88.5 192 19.933333333333334 193 112.90694444444445 194 20.215254237288136 195 95.08250000000001 196 24.474999999999998 197 110.5042372881356 198 111.68958333333333 199 20.75 200 99.30185185185185 201 79.45 202 104.30281690140845 203 79.53461538461539 204 67.24886363636364 205 81.35909090909091 206 58.044444444444444 207 79.9 208 101.81315789473685 209 103.9703125 210 42.25 211 25.25 212 18.42950819672131 213 18.622413793103448 214 85.90652173913043 215 60.30614035087719 216 43.608333333333334 217 57.41212121212121 218 81.91538461538461 2

### Set Custom Split - Random Split

If you prefer AutoML to split the dataset with a different ratio than **the default 60:20:20**, you can create a new column in your dataset with the desired split assignments. This column **should contain the values "train", "validate", or "test"** to designate each row's role. When invoking the AutoML API, pass this column to the `split_col` parameter.

This approach allows you to define custom data splits tailored to your specific requirements. Ensure that the `custom_split` column accurately reflects the intended distribution of your data into training, validation, and test sets. 

> _Example for understanding the code below: Consider the three values 0.5, 0.8, and 0.91 that are each mapped to three different rows. We will consider the row containing 0.5 as a _train_ data point, while 0.8 is considered a _validation_ data point and 0.91 as a _test_ data point. Basically, values in the interval [0, 0.79] belong to the training dataset, values between [0.8, 0.89] belong to the validation set, and values between [0.9, 1.0] belong to the test set._

In [0]:
from pyspark.sql.functions import when, rand

dataset = spark.read.table("customer_churn")

seed = 42 # define your seed here for reproduction
train_ratio, validate_ratio, test_ratio = 0.8, 0.1, 0.1 # define your preferred ratios here

dataset = dataset.withColumn("random", rand(seed=seed))
dataset = dataset.withColumn("custom_split", when(dataset.random < train_ratio, "train")
                                    .when(dataset.random < 1-test_ratio, "validate")
                                    .otherwise("test"))
dataset = dataset.drop("random")
display(dataset)

CustomerID Gender SeniorCitizen Partner InternetService Contract PaperlessBilling PaymentMethod Churn custom_split 0 Female 0 Yes DSL Month-to-month Yes Electronic check No train 1 Male 0 No DSL One year No Mailed check No train 2 Male 0 No DSL Month-to-month Yes Mailed check Yes validate 3 Male 0 No DSL One year No Bank transfer (automatic) No train 4 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes train 5 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes train 6 Male 0 No Fiber optic Month-to-month Yes Credit card (automatic) No test 7 Female 0 No DSL Month-to-month No Mailed check No train 8 Female 0 Yes Fiber optic Month-to-month Yes Electronic check Yes test 9 Male 0 No DSL One year No Bank transfer (automatic) No train 10 Male 0 Yes DSL Month-to-month Yes Mailed check No train 11 Male 0 No No Two year No Credit card (automatic) No train 12 Male 0 Yes Fiber optic One year No Credit card (automatic) No train 13 Male 0 No Fiber optic Month-to-month Yes Bank transfer (automatic) Yes validate 14 Male 0 No Fiber optic Month-to-month Yes Electronic check No train 15 Female 0 Yes Fiber optic Two year No Credit card (automatic) No train 16 Female 0 No No One year No Mailed check No train 17 Male 0 No Fiber optic Two year No Bank transfer (automatic) No train 18 Female 0 Yes DSL Month-to-month No Credit card (automatic) Yes train 19 Female 0 No Fiber optic Month-to-month Yes Electronic check No validate 20 Male 1 No DSL Month-to-month Yes Electronic check Yes train 21 Male 0 Yes No One year No Bank transfer (automatic) No train 22 Male 0 No No Month-to-month No Mailed check Yes train 23 Female 0 Yes DSL Two year Yes Credit card (automatic) No validate 24 Male 0 Yes DSL Month-to-month No Credit card (automatic) No train 25 Female 0 No DSL Month-to-month Yes Bank transfer (automatic) No train 26 Male 0 Yes Fiber optic Month-to-month Yes Electronic check Yes train 27 Male 0 Yes DSL Month-to-month No Electronic check Yes train 28 Male 0 Yes DSL Two year Yes Credit card (automatic) No train 29 Female 0 No DSL Month-to-month Yes Mailed check Yes validate 30 Female 1 Yes Fiber optic Two year Yes Credit card (automatic) No train 31 Male 1 Yes Fiber optic Month-to-month Yes Credit card (automatic) No train 32 Female 0 Yes DSL One year No Mailed check No train 33 Male 0 No No Month-to-month No Bank transfer (automatic) No train 34 Male 1 No DSL Month-to-month No Bank transfer (automatic) No train 35 Female 0 Yes Fiber optic Two year No Bank transfer (automatic) No validate 36 Male 0 No Fiber optic Month-to-month Yes Electronic check Yes train 37 Female 0 No Fiber optic Month-to-month Yes Credit card (automatic) No train 38 Male 0 No Fiber optic Month-to-month Yes Electronic check Yes train 39 Female 0 No Fiber optic Month-to-month Yes Bank transfer (automatic) Yes train 40 Male 0 Yes DSL One year No Mailed check No train 41 Female 0 Yes DSL Two year Yes Credit card (automatic) No train 42 Female 0 Yes No One year No Mailed check No train 43 Female 0 No DSL Two year Yes Credit card (automatic) No train 44 Female 0 Yes DSL Month-to-month Yes Electronic check No train 45 Female 0 No Fiber optic Month-to-month Yes Electronic check No validate 46 Male 0 No DSL Month-to-month No Mailed check No validate 47 Female 0 No Fiber optic Month-to-month Yes Electronic check Yes test 48 Male 0 No DSL Two year Yes Credit card (automatic) No train 49 Female 0 Yes DSL Two year Yes Credit card (automatic) No validate 50 Female 1 No Fiber optic Month-to-month Yes Electronic check No train 51 Female 0 No Fiber optic Month-to-month Yes Credit card (automatic) Yes validate 52 Female 1 Yes DSL Month-to-month Yes Credit card (automatic) No train 53 Female 1 Yes Fiber optic Month-to-month Yes Credit card (automatic) Yes train 54 Female 1 Yes DSL One year Yes Credit card (automatic) No train 55 Male 1 No Fiber optic Month-to-month Yes Electronic check Yes test 56 Female 0 Yes Fiber optic One year Yes Credit card (automatic) No train 57 Ma

 **Further Reading: Stratified Sampling with AutoML**

Stratified sampling ensures that the distribution of a categorical variable (e.g., target labels) is preserved across the training, validation, and test sets. This is particularly useful when dealing with imbalanced datasets.

1. **Identify the Stratification Column** – Choose a categorical variable to maintain proportions across dataset splits.

2. **Compute Class Proportions** – Determine the distribution of each category in the dataset.

3. **Calculate Sample Sizes** – Apply the desired split ratios to compute the exact number of records per class for each split.

4. **Perform Stratified Sampling** – Split each category proportionally into training, validation, and test sets.

5. **Assign Labels and Combine Splits** – Label the subsets accordingly and merge them into the final dataset.

6. **Validate Class Distribution** – Ensure each split maintains the original class proportions.

**Sample Code**

```from pyspark.sql.functions import count, lit, col, round

# Load dataset
dataset = spark.read.table("customer_churn")

# Define stratification column
stratify_col = "Gender"

# Define split ratios
train_ratio, validate_ratio, test_ratio = 0.8, 0.1, 0.1
seed = 42

# Step 1: Compute class counts and original distribution
class_counts = dataset.groupBy(stratify_col).agg(count("*").alias("count"))

original_distribution = (
    class_counts.withColumn("percentage", round((col("count") / dataset.count()) * 100, 2))
    .withColumn("dataset", lit("original"))
)

# Step 2: Perform stratified sampling
train_df = dataset.sampleBy(stratify_col, {row[stratify_col]: train_ratio for row in class_counts.collect()}, seed)
validate_df = dataset.subtract(train_df).sampleBy(
    stratify_col, {row[stratify_col]: validate_ratio / (validate_ratio + test_ratio) for row in class_counts.collect()}, seed
)
test_df = dataset.subtract(train_df).subtract(validate_df)

# Assign split labels
train_df = train_df.withColumn("custom_split", lit("train"))
validate_df = validate_df.withColumn("custom_split", lit("validate"))
test_df = test_df.withColumn("custom_split", lit("test"))

# Combine datasets efficiently
final_dataset = train_df.unionByName(validate_df).unionByName(test_df)

# Step 4: Validate stratification with correct percentage calculation
def validate_distribution(df, split_name):
    total_split_count = df.count()
    return (
        df.groupBy(stratify_col)
        .agg(count("*").alias("count"))
        .withColumn("dataset", lit(split_name))
        .withColumn("percentage", round((col("count") / total_split_count) * 100, 2))
    )

# Compute distributions
train_dist = validate_distribution(train_df, "train")
validate_dist = validate_distribution(validate_df, "validate")
test_dist = validate_distribution(test_df, "test")

# **Ensure Schema Consistency Before Union**
columns_order = ["Gender", "count", "percentage", "dataset"]

original_distribution = original_distribution.select(*columns_order)
train_dist = train_dist.select(*columns_order)
validate_dist = validate_dist.select(*columns_order)
test_dist = test_dist.select(*columns_order)

# Combine all distributions (original + splits)
distribution_comparison = original_distribution.unionByName(train_dist).unionByName(validate_dist).unionByName(test_dist)

# Display the final distribution comparison
display(distribution_comparison)
```

### Start an Experiment

Now that we have **feature lookups** and **custom splits column** ready, we can continue to setup an AutoML experiment.

In [0]:
from databricks import automl
from datetime import datetime

automl_run = automl.classify(
    dataset = dataset,
    target_col = "Churn",
    split_col = "custom_split",
    exclude_cols = ["CustomerID"], # Exclude columns as needed
    timeout_minutes = 5,
    feature_store_lookups = feauture_store_lookups
)

2025/08/07 04:44:05 INFO databricks.automl.client.manager: AutoML will optimize for F1 score metric, which is tracked as val_f1_score in the MLflow experiment.
2025/08/07 04:44:06 INFO databricks.automl.client.manager: MLflow Experiment ID: 4297320214106179
2025/08/07 04:44:06 INFO databricks.automl.client.manager: MLflow Experiment: https://dbc-8b9f7bce-656b.cloud.databricks.com/?o=182135318479115#mlflow/experiments/4297320214106179
2025/08/07 04:45:19 INFO databricks.automl.client.manager: Data exploration notebook: https://dbc-8b9f7bce-656b.cloud.databricks.com/?o=182135318479115#notebook/4297320214106184
2025/08/07 04:49:42 INFO databricks.automl.client.manager: AutoML experiment completed successfully.


For exploratory data analysis, open the data exploration notebook 
 To view the best performing model, open the best trial notebook 
 To view details about all trials, navigate to the MLflow experiment 
 Metrics for the best trial: 
 
 <!-- class inlined from webapp/web/js/templates/iframeSandbox.css -->
 
 
 
 
 
 Train 
 Validation 
 Test 
 
 
 
 
 
 f1_score 
 0.580 
 0.630 
 0.542 
 
 

 
 recall_score 
 0.625 
 0.663 
 0.558 
 
 

 
 roc_auc 
 0.790 
 0.804 
 0.769 
 
 

 
 false_negatives 
 562.000 
 61.000 
 84.000 
 
 

 
 false_positives 
 791.000 
 80.000 
 95.000 
 
 

 
 example_count 
 5698.000 
 643.000 
 702.000 
 
 

 
 precision_score 
 0.542 
 0.600 
 0.527 
 
 

 
 true_positives 
 936.000 
 120.000 
 106.000 
 
 

 
 precision_recall_auc 
 0.486 
 0.536 
 0.470 
 
 

 
 true_negatives 
 3409.000 
 382.000 
 417.000 
 
 

 
 log_loss 
 0.458 
 0.462 
 0.485 
 
 

 
 score 
 0.763 
 0.781 
 0.745 
 
 

 
 accuracy_score 
 0.763 
 0.781 
 0.745

### Search for the Best Run

The search for the best run in this experiment, we need to first **get the experiment ID** and then **search for the runs** by experiment.

In [0]:
import mlflow
# Get the experiment path by experiment ID
exp_path = mlflow.get_experiment(automl_run.experiment.experiment_id).name
# Find the most recent experiment in the AutoML folder
filter_string=f'name LIKE "{exp_path}"'
automl_experiment_id = mlflow.search_experiments(
  filter_string=filter_string,
  max_results=1,
  order_by=["last_update_time DESC"])[0].experiment_id

In [0]:
from mlflow.entities import ViewType

# Find the best run ...
automl_runs_pd = mlflow.search_runs(
  experiment_ids=[automl_experiment_id],
  filter_string=f"attributes.status = 'FINISHED'",
  run_view_type=ViewType.ACTIVE_ONLY,
  order_by=["metrics.val_f1_score DESC"]
)


**Print information about the best trial from the AutoML experiment.**


In [0]:
print(automl_run.best_trial)


Model: TransformedTargetClassifier(classifier=XGBClassifier(base_score=None,
                                             booster=None,
                                             callbacks=None,
                                             colsample_bylevel=None,
                                             colsample_bynode=None,
                                             colsample_bytree=0.21139987766023793,
                                             device=None,
                                             early_stopping_rounds=None,
                                             enable_categorical=False,
                                             eval_metric=None,
                                             feature_types=None,
                                             gamma=None,
                                             grow_policy=None,
                                             importance_type=None,
                                             interaction_constrai

**Explanation**


- **`print(automl_run.best_trial)`**: This prints information about the best trial or run from the AutoML experiment.

    - **Model:** Specifies the machine learning model that performed the best. 

    - **Model path:** The MLflow artifact URL of the model trained in this trial.

    - **Preprocessors:** Description of the preprocessors run before training the model.

    - **Training duration:** Displays the duration it took to train the best model.

    - **Evaluation metric score:** Shows the value of the evaluation metric used to determine the best model. 

    - **Evaluation metric:** Score of primary metric, evaluated for the validation dataset.

**Import notebooks for other runs in AutoML.**

For classification and regression experiments, AutoML generated notebooks for data exploration and the best trial in your experiment are automatically imported to your workspace. Generated notebooks for other experiment trials are saved as MLflow artifacts on DBFS instead of auto-imported into your workspace. 

For all trials besides the best trial, the **`notebook_path`** and **`notebook_url`** in the TrialInfo Python API are not set. If you need to use these notebooks, you can manually import them into your workspace with the AutoML experiment UI or the **`automl.import_notebook`** Python API.

**🚨 Notice:** `destination_path` takes Workspace as root.

In [0]:
# Create the Destination path for storing the best run notebook
destination_path = f"/Users/{DA.username}/imported_notebooks/demo-3.1-{datetime.now().strftime('%Y%m%d%H%M%S')}"

# Get the path and url for the generated notebook
result = automl.import_notebook(automl_run.trials[1].artifact_uri, destination_path)
print(f"The notebook is imported to: {result.path}")
print(f"The notebook URL           : {result.url}")

The notebook is imported to: /Users/labuser11091541_1754532261@vocareum.com/imported_notebooks/demo-3.1-20250807042925
The notebook URL           : https://dbc-8b9f7bce-656b.cloud.databricks.com/?o=182135318479115/#workspace/Users/labuser11091541_1754532261@vocareum.com/imported_notebooks/demo-3.1-20250807042925



## Conclusion

In this demo, we show how to use AutoML UI and AutoML API for creating classification model and how we can retrieve the best run and access the generated notebook, and how we can modify the parameters of the best model. 



&copy; 2025 Databricks, Inc. All rights reserved. Apache, Apache Spark, Spark, the Spark Logo, Apache Iceberg, Iceberg, and the Apache Iceberg logo are trademarks of the <a href="https://www.apache.org/" target="blank">Apache Software Foundation</a>.<br/>
<br/><a href="https://databricks.com/privacy-policy" target="blank">Privacy Policy</a> | 
<a href="https://databricks.com/terms-of-use" target="blank">Terms of Use</a> | 
<a href="https://help.databricks.com/" target="blank">Support</a>